In [45]:
from collections import OrderedDict
from tqdm.notebook import tnrange, tqdm
import pandas as pd
from cesium.time_series import TimeSeries
import cesium.featurize as featurize
import numpy as np
import schwimmbad
from astropy.table import Table
from astropy.io import fits as pf

In [2]:
features_to_use = ["amplitude",
                   "percent_beyond_1_std",
                   "maximum",
                   "max_slope",
                   "median",
                   "median_absolute_deviation",
                   "percent_close_to_median",
                   "minimum",
                   "skew",
                   "std",
                   "weighted_average"]

def worker(tsobj):
    global features_to_use
    thisfeats = featurize.featurize_single_ts(tsobj,\
    features_to_use=features_to_use,
    raise_exceptions=False)
    return thisfeats

In [3]:
lc_data = pd.read_pickle('/home/nmiranda/workspace/ztf_rapid/data/raw/rcf_marshallc_sncosmo_200114_2018classupdate_addedcv.pkl')

In [55]:
y = {id_: lightcurve.meta['classification'] for id_, lightcurve in lc_data.items()}
y = pd.Series(y)
y

ZTF19abjrkqn     SN Ia
ZTF18acdxhus     SN Ia
ZTF19aayjhpg     SN II
ZTF18acbwxgn     SN Ia
ZTF19acaqqng    SN II?
                 ...  
ZTF18accnmri     SN II
ZTF18acbuwcq      None
ZTF18acbvuli      None
ZTF18accpnbj      None
ZTF18aceynvm     SN Ia
Length: 4578, dtype: object

In [4]:
keys = list(lc_data.keys())
nobjects = len(keys)
pbmap = OrderedDict([(1,'p48g'), (2,'p48r'), (3,'p48i')])
pbnames = list(pbmap.values())

In [5]:
tsdict = OrderedDict()
for idx in tnrange(nobjects, desc='Building Timeseries'):
    ztfid = keys[idx]
    this_lc = lc_data[ztfid]
    if len(this_lc) < 2:
        continue
    thisid = ztfid
    target = this_lc.meta['classification']
    try:
        this_z = this_lc['z']
    except KeyError:
        this_z = None
    try:
        this_mwevb = this_lc['mwebv']
    except KeyError:
        this_mwebv = None
    
    meta = {'z':this_z,\
            'mwebv':this_mwebv}
    
#     ind = (lcdata['object_id'] == thisid)
#     thislc = lcdata[ind]
    pbnames = set(this_lc['band'])

    pbind = [(this_lc['band'] == pb) for pb in pbnames]
    t = [this_lc['mjd'][mask].data for mask in pbind ]
    m = [this_lc['flux'][mask].data for mask in pbind]
    e = [this_lc['fluxerr'][mask].data for mask in pbind ]

    tsdict[ztfid] = TimeSeries(t=t, m=m, e=e,\
                        label=target, name=thisid, meta_features=meta,\
                        channel_names=pbnames )

Building Timeseries:   0%|          | 0/4578 [00:00<?, ?it/s]

In [6]:
features_list = []
with tqdm(total=len(tsdict), desc="Computing Features") as pbar:
    with schwimmbad.MultiPool() as pool:  
        results = pool.imap(worker, list(tsdict.values()))
        for res in results:
            features_list.append(res)
            pbar.update()

Computing Features:   0%|          | 0/4572 [00:00<?, ?it/s]

/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/cesium/features/lomb_scargle.py:256: RuntimeWarning: invalid value encountered in sqrt
  damp = np.sqrt(A0**2 * vA0 + B0**2 * vB0 + 2. * A0 * B0 * covA0B0) / amp
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/cesium/features/lomb_scargle.py:266: RuntimeWarning: invalid value encountered in sqrt
  dphase[j] = np.sqrt(np.dot(np.dot(v, m), v))
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/cesium/features/scatter_res_raw.py:14: RuntimeWarning: divide by zero encountered in double_scalars
  cf.median_absolute_deviation(m))
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/numpy/core/fromnumeric.py:3373: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/cesium/features/cadence_features.py:12: RuntimeWarning: divide by zero encountered in true_divide
  return (cads[2:] + cads[:-2]) / (c

/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/cesium/features/scatter_res_raw.py:14: RuntimeWarning: divide by zero encountered in double_scalars
  cf.median_absolute_deviation(m))
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/cesium/features/lomb_scargle.py:250: RuntimeWarning: divide by zero encountered in true_divide
  vmodl = vcn/s0 + np.dot((hat_matr/wth0).T, np.dot(hat_hat, hat_matr/wth0))
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/cesium/features/scatter_res_raw.py:14: RuntimeWarning: divide by zero encountered in double_scalars
  cf.median_absolute_deviation(m))
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/cesium/features/period_folding.py:88: RuntimeWarning: invalid value encountered in double_scalars
  out_dict['scatter_over_mad'] = median_diff / mad
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/cesium/features/period_folding.py:91: RuntimeWarning: invalid va

/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/cesium/features/period_folding.py:88: RuntimeWarning: invalid value encountered in double_scalars
  out_dict['scatter_over_mad'] = median_diff / mad
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/cesium/features/period_folding.py:88: RuntimeWarning: invalid value encountered in double_scalars
  out_dict['scatter_over_mad'] = median_diff / mad
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/cesium/features/period_folding.py:91: RuntimeWarning: invalid value encountered in double_scalars
  out_dict['scatter_pfold_over_mad'] = median_1per_fold_diff / mad
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/cesium/features/scatter_res_raw.py:14: RuntimeWarning: divide by zero encountered in double_scalars
  cf.median_absolute_deviation(m))
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/cesium/features/period_folding.py:91: RuntimeWarning: inv

/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/numpy/core/fromnumeric.py:3373: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/cesium/features/lomb_scargle.py:50: RuntimeWarning: invalid value encountered in double_scalars
  numf = int((fmax - f0) / df) # TODO !!! this is off by 1 point, fix?
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/cesium/features/lomb_scargle.py:47: RuntimeWarning: divide by zero encountered in double_scalars
  f0 = 1. / max(time)
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/cesium/features/lomb_scargle.py:48: RuntimeWarning: divide by zero encountered in double_scalars
  df = 0.8 / max(time) # 20120202 :    0.1/Xmax
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/cesium/features/scatter_res_raw.py:14: RuntimeWarning: divide by zero encountered in double_scalars
  cf.median_absolute_deviation(m))

...

/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/numpy/core/fromnumeric.py:3373: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/cesium/features/cadence_features.py:41: RuntimeWarning: invalid value encountered in true_divide
  return hist / (total_time * np.mean(hist))
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/numpy/core/_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/numpy/core/_methods.py:234: RuntimeWarning: Degrees of freedom <= 0 for slice
  keepdims=keepdims)
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/numpy/core/_methods.py:195: RuntimeWarning: invalid value encountered in true_divide
  arrmean, rcount, out=arrmean, casting='unsafe', subok=False)
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python

/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/cesium/features/scatter_res_raw.py:14: RuntimeWarning: divide by zero encountered in double_scalars
  cf.median_absolute_deviation(m))
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/cesium/features/period_folding.py:88: RuntimeWarning: invalid value encountered in double_scalars
  out_dict['scatter_over_mad'] = median_diff / mad
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/numpy/core/fromnumeric.py:3373: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/cesium/features/period_folding.py:91: RuntimeWarning: divide by zero encountered in double_scalars
  out_dict['scatter_pfold_over_mad'] = median_1per_fold_diff / mad
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/numpy/core/_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret 

/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/numpy/core/_methods.py:226: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/numpy/core/fromnumeric.py:3373: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/numpy/core/_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/numpy/core/_methods.py:234: RuntimeWarning: Degrees of freedom <= 0 for slice
  keepdims=keepdims)
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/numpy/core/_methods.py:195: RuntimeWarning: invalid value encountered in true_divide
  arrmean, rcount, out=arrmean, casting='unsafe', subok=False)
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages

/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/gatspy/periodic/optimizer.py:88: RuntimeWarning: divide by zero encountered in double_scalars
  omega_min = 2 * np.pi / np.max(self.period_range)
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/cesium/features/amplitude.py:37: RuntimeWarning: invalid value encountered in double_scalars
  return (y_95 - y_5) / y_50
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/gatspy/periodic/optimizer.py:89: RuntimeWarning: divide by zero encountered in double_scalars
  omega_max = 2 * np.pi / np.min(self.period_range)
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/gatspy/periodic/optimizer.py:90: RuntimeWarning: invalid value encountered in double_scalars
  omegas = np.arange(omega_min, omega_max + omega_step, omega_step)
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/cesium/features/lomb_scargle.py:47: RuntimeWarning: divide by zero encountered i

/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/cesium/features/lomb_scargle.py:235: RuntimeWarning: invalid value encountered in double_scalars
  out_dict['psd'] = psd[j] * 0.5 / varcn
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/cesium/features/lomb_scargle.py:278: RuntimeWarning: invalid value encountered in double_scalars
  prob = stats.f.sf(0.5 * (ntime - 1. - detrend_order) * (1. -out_dict['chi2'] / out_dict['chi0']), 2, ntime - 1 - detrend_order)
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/numpy/core/fromnumeric.py:3373: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/numpy/core/_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
/home/nmiranda/miniconda3/envs/ztf_rapid/lib/python3.6/site-packages/numpy/core/_methods.py:234: RuntimeWarning: Degrees of freedom <= 0 for sli

In [9]:
features_list[0]

feature                    channel
amplitude                  0          214.274260
                           1          218.257916
percent_beyond_1_std       0            0.333333
                           1            0.357143
maximum                    0          428.548520
                           1          436.515832
max_slope                  0           51.804200
                           1           37.883785
median                     0            0.000000
                           1            0.000000
median_absolute_deviation  0            0.000000
                           1            0.000000
percent_close_to_median    0            0.533333
                           1            0.642857
minimum                    0            0.000000
                           1            0.000000
skew                       0            0.520028
                           1            0.771352
std                        0          179.426538
                           1      

In [11]:
featuretable = featurize.assemble_featureset(features_list=features_list,\
                              time_series=tsdict.values())

In [12]:
featuretable

feature        amplitude                                                  \
channel                0           1           2   3   4   5   6   7   8   
ZTF19abjrkqn  214.274260  218.257916         NaN NaN NaN NaN NaN NaN NaN   
ZTF18acdxhus   90.378314  183.218787         NaN NaN NaN NaN NaN NaN NaN   
ZTF19aayjhpg   71.861732   42.602003         NaN NaN NaN NaN NaN NaN NaN   
ZTF18acbwxgn  226.448790  123.301967  210.363314 NaN NaN NaN NaN NaN NaN   
ZTF19acaqqng  173.368425   53.609733         NaN NaN NaN NaN NaN NaN NaN   
...                  ...         ...         ...  ..  ..  ..  ..  ..  ..   
ZTF18accnmri  257.614322   75.678062         NaN NaN NaN NaN NaN NaN NaN   
ZTF18acbuwcq  108.443624   33.712058         NaN NaN NaN NaN NaN NaN NaN   
ZTF18acbvuli  151.199911  375.811447         NaN NaN NaN NaN NaN NaN NaN   
ZTF18accpnbj    3.753019         NaN         NaN NaN NaN NaN NaN NaN NaN   
ZTF18aceynvm  330.346724  315.478672         NaN NaN NaN NaN NaN NaN NaN   

feature          max_slope  ... weighted_average                              \
channel                  0  ...                1           2   3   4   5   6   
ZTF19abjrkqn     51.804200  ...        40.882919         NaN NaN NaN NaN NaN   
ZTF18acdxhus     32.261915  ...       146.230868         NaN NaN NaN NaN NaN   
ZTF19aayjhpg     10.263904  ...       273.090263         NaN NaN NaN NaN NaN   
ZTF18acbwxgn  20692.472606  ...       177.625108  244.738621 NaN NaN NaN NaN   
ZTF19acaqqng  70113.866087  ...       291.435655         NaN NaN NaN NaN NaN   
...                    ...  ...              ...         ...  ..  ..  ..  ..   
ZTF18accnmri  62814.501877  ...        52.428038         NaN NaN NaN NaN NaN   
ZTF18acbuwcq     37.126438  ...       326.263694         NaN NaN NaN NaN NaN   
ZTF18acbvuli     25.212285  ...       134.368932         NaN NaN NaN NaN NaN   
ZTF18accpnbj      2.502179  ...              NaN         NaN NaN NaN NaN NaN   
ZTF18aceynvm   4311.291258  ...       133.474175         NaN NaN NaN NaN NaN   

feature                  z mwebv  
channel        7   8              
ZTF19abjrkqn NaN NaN  None  None  
ZTF18acdxhus NaN NaN  None  None  
ZTF19aayjhpg NaN NaN  None  None  
ZTF18acbwxgn NaN NaN  None  None  
ZTF19acaqqng NaN NaN  None  None  
...           ..  ..   ...   ...  
ZTF18accnmri NaN NaN  None  None  
ZTF18acbuwcq NaN NaN  None  None  
ZTF18acbvuli NaN NaN  None  None  
ZTF18accpnbj NaN NaN  None  None  
ZTF18aceynvm NaN NaN  None  None  

[4572 rows x 101 columns]

In [49]:
old_names = featuretable.columns.values
new_names = ['{}_{}'.format(x, pbmap.get(y,'meta')) for x,y in old_names]
new_names_dict = {'{}_{}'.format(x, pbmap.get(y,'meta')): (x,y) for x, y in old_names}
new_names_dict.pop('z_meta')
new_names_dict.pop('mwebv_meta')
cols = [featuretable[col] for col in new_names_dict.values()]
allfeats = Table(cols, names=new_names_dict.keys())
allfeats

<Table length=4572>
amplitude_meta   amplitude_p48g   ... weighted_average_p48i
   float64          float64       ...        float64       
-------------- ------------------ ... ---------------------
           nan 218.25791612008328 ...                   nan
           nan 183.21878732391667 ...                   nan
           nan  42.60200274174288 ...                   nan
           nan 123.30196686171706 ...                   nan
           nan 53.609733039768244 ...                   nan
           nan 181.51358860161557 ...     371.3623966753124
           nan  272.2513264212107 ...                   nan
           nan 136.34068697762265 ...                   nan
           nan 382.79830345562846 ...                   nan
           nan  56.16371880482386 ...                   nan
           ...                ... ...                   ...
           nan 51.362080519256224 ...                   nan
           nan                nan ...                   nan
           nan 1104.0023665094495 ...                   nan
           nan  124.4428659141194 ...                   nan
           nan 186.93935663142247 ...                   nan
           nan  75.67806242181035 ...                   nan
           nan  33.71205772723121 ...                   nan
           nan  375.8114470091034 ...                   nan
           nan                nan ...                   nan
           nan 315.47867224009684 ...                   nan

In [56]:
coldefs = list()
coldefs.append(pf.Column(name='ztfid', format='12A', array=np.array(featuretable.index)))
for idx, colname in enumerate(allfeats.columns):
    coldefs.append(pf.Column(name=colname, format='F', array=allfeats[colname]))
coldefs.append(pf.Column(name='target', format='16A', array=y[featuretable.index]))
tbhdu = pf.BinTableHDU.from_columns(coldefs)
tbhdu.writeto('/home/nmiranda/workspace/ztf_rapid/data/interim/rcf_cesium_features.fits', checksum=True, overwrite=True)